#### This notebook focuses on various ways to tokenize and digest symptoms data (data joined from VAERSDATA and VAERSVAX over Covid ). 
#### -Ollama Performance
#### -en_ner_bc5cdr_md model

SNEHA DHARNE

In [2]:
import numpy as numpy
import pandas as pd

In [ ]:
df_vax = pd.read_csv('2024VAERSVAX.csv', encoding='latin1')

In [ ]:
#getting an estimate of number of data points for covid19 vaccine
df_vax.VAX_TYPE.value_counts().head(16)

VAX_TYPE
COVID19      15920
VARZOS        5298
RSV           2924
FLU3          2233
TDAP          1886
PNC20         1682
COVID19-2     1636
HEP           1592
FLU4          1533
HPV9          1520
VARCEL        1387
HEPA          1334
MMR           1321
MNQ           1238
MMRV          1215
UNK           1103
Name: count, dtype: int64

In [11]:
df_data = pd.read_csv('2024VAERSDATA.csv', encoding='latin1')


In [ ]:
df_data #symptoms free text

VAERS_ID    RECVDATE STATE  AGE_YRS  CAGE_YR  CAGE_MO SEX RPT_DATE   
0       2728969  01/01/2024    AK     14.0      NaN      NaN   M      NaN  \
1       2728982  01/01/2024    NJ      NaN      NaN      NaN   U      NaN   
2       2728984  01/01/2024   NaN      NaN      NaN      NaN   U      NaN   
3       2728992  01/01/2024    MO      NaN      NaN      NaN   F      NaN   
4       2728993  01/01/2024   NaN      NaN      NaN      NaN   U      NaN   
...         ...         ...   ...      ...      ...      ...  ..      ...   
41832   2802236  10/25/2024   NaN     71.0     71.0      NaN   F      NaN   
41833   2802237  10/25/2024   NaN     39.0     38.0      NaN   F      NaN   
41834   2802238  10/25/2024   NaN     80.0     80.0      NaN   M      NaN   
41835   2802239  10/25/2024   NaN     35.0     35.0      NaN   M      NaN   
41836   2802240  10/25/2024   NaN     43.0     43.0      NaN   F      NaN   

                                            SYMPTOM_TEXT DIED  ...   
0      fluzone qiv hd administered to a minor patient...  NaN  ...  \
1      administering vaccines subcutaneously to patie...  NaN  ...   
2      extreme joint pain; Unable to walk; This non-s...  NaN  ...   
3      was due to have 2nd when everything shut down ...  NaN  ...   
4      Injection site hot; Hypersentivity reaction; C...  NaN  ...   
...                                                  ...  ...  ...   
41832  Covid Pfizer Vaccine was stored in the freezer...  NaN  ...   
41833  Covid Pfizer Vaccine was stored in the freezer...  NaN  ...   
41834  Covid Pfizer Vaccine was stored in the freezer...  NaN  ...   
41835  Covid Pfizer Vaccine was stored in the freezer...  NaN  ...   
41836  Covid Pfizer Vaccine was stored in the freezer...  NaN  ...   

                                                 CUR_ILL HISTORY PRIOR_VAX   
0                                                    NaN     NaN       NaN  \
1                                                    NaN     NaN       NaN   
2                                                    NaN     NaN       NaN   
3                                                    NaN     NaN       NaN   
4      Autoimmune disorder (Autoimmune disorder diagn...     NaN       NaN   
...                                                  ...     ...       ...   
41832                                                NaN     NaN       NaN   
41833                                                NaN     NaN       NaN   
41834                                                NaN     NaN       NaN   
41835                                                NaN     NaN       NaN   
41836                                                NaN     NaN       NaN   

                   SPLTTYPE  FORM_VERS TODAYS_DATE BIRTH_DEFECT OFC_VISIT   
0          USSA2023SA396019          2  12/30/2023          NaN       NaN  \
1      USGSKUS2023AMR179885          2  01/01/2024          NaN       NaN   
2      USGSKUS2023AMR180978          2  01/01/2024          NaN       NaN   
3      USGSKUS2023AMR181463          2  01/01/2024          NaN       NaN   
4      USGSKUS2023AMR181703          2  01/01/2024          NaN       NaN   
...                     ...        ...         ...          ...       ...   
41832                   NaN          2         NaN          NaN       NaN   
41833                   NaN          2         NaN          NaN       NaN   
41834                   NaN          2         NaN          NaN       NaN   
41835                   NaN          2         NaN          NaN       NaN   
41836                   NaN          2         NaN          NaN       NaN   

      ER_ED_VISIT ALLERGIES  
0             NaN       NaN  
1             NaN       NaN  
2             NaN       NaN  
3             NaN       NaN  
4             NaN       NaN  
...           ...       ...  
41832         NaN       NaN  
41833         NaN       NaN  
41834         NaN       NaN  
41835         NaN       NaN  
41836         NaN       NaN  

[41837 rows x 35 c

In [3]:
df_symp = pd.read_csv('2024VAERSSYMPTOMS.csv', encoding='latin1')

In [ ]:
df_symp #symptoms columns

VAERS_ID                                   SYMPTOM1  SYMPTOMVERSION1   
0       2728969  Incorrect route of product administration             26.1  \
1       2728982  Incorrect route of product administration             26.1   
2       2728984                                 Arthralgia             26.1   
3       2728992           Incomplete course of vaccination             26.1   
4       2728993                 Body temperature increased             26.1   
...         ...                                        ...              ...   
51507   2802236                      Product storage error             27.1   
51508   2802237                      Product storage error             27.1   
51509   2802238                      Product storage error             27.1   
51510   2802239                      Product storage error             27.1   
51511   2802240                      Product storage error             27.1   

               SYMPTOM2  SYMPTOMVERSION2   
0      No adverse event             26.1  \
1                   NaN              NaN   
2        Gait inability             26.1   
3                   NaN              NaN   
4                Chills             26.1   
...                 ...              ...   
51507               NaN              NaN   
51508               NaN              NaN   
51509               NaN              NaN   
51510               NaN              NaN   
51511               NaN              NaN   

                                                SYMPTOM3  SYMPTOMVERSION3   
0      Product administered to patient of inappropria...             26.1  \
1                                                    NaN              NaN   
2                                                    NaN              NaN   
3                                                    NaN              NaN   
4                                               Erythema             26.1   
...                                                  ...              ...   
51507                                                NaN              NaN   
51508                                                NaN              NaN   
51509                                                NaN              NaN   
51510                                                NaN              NaN   
51511                                                NaN              NaN   

                                 SYMPTOM4  SYMPTOMVERSION4          SYMPTOM5   
0              Wrong product administered             26.1               NaN  \
1                                     NaN              NaN               NaN   
2                                     NaN              NaN               NaN   
3                                     NaN              NaN               NaN   
4      Feeling of body temperature change             26.1  Hypersensitivity   
...                                   ...              ...               ...   
51507                                 NaN              NaN               NaN   
51508                                 NaN              NaN               NaN   
51509                                 NaN              NaN               NaN   
51510                                 NaN              NaN               NaN   
51511                                 NaN              NaN               NaN   

       SYMPTOMVERSION5  
0                  NaN  
1                  NaN  
2                  NaN  
3                  NaN  
4                 26.1  
...                ...  
51507              NaN  
51508              NaN  
51509              NaN  
51510              NaN  
51511              NaN  

[51512 rows x 11 columns]

In [ ]:

#this dataset was later provided by Gunik after performing join and merge on vaersvax and vaersdata datasets

df_symptoms_covid = pd.read_csv('symptoms_covid.csv')

In [10]:
df_symptoms_covid

Unnamed: 0  VAERS_ID VAX_TYPE   
0               0   2728994  COVID19  \
1               1   2729004  COVID19   
2               2   2729006  COVID19   
3               3   2729006  COVID19   
4               4   2729006  COVID19   
...           ...       ...      ...   
17420       17551   2802236  COVID19   
17421       17552   2802237  COVID19   
17422       17553   2802238  COVID19   
17423       17554   2802239  COVID19   
17424       17555   2802240  COVID19   

                                            SYMPTOM_TEXT V_ADMINBY  FORM_VERS  
0      muscle at the injection site is sore; He canno...       PHM          2  
1      Micro-seizures starting approximately 2 weeks ...       OTH          2  
2      On September 14, 2023, I was admitted to Hospi...       PHM          2  
3      On September 14, 2023, I was admitted to Hospi...       PHM          2  
4      On September 14, 2023, I was admitted to Hospi...       PHM          2  
...                                                  ...       ...        ...  
17420  Covid Pfizer Vaccine was stored in the freezer...       UNK          2  
17421  Covid Pfizer Vaccine was stored in the freezer...       UNK          2  
17422  Covid Pfizer Vaccine was stored in the freezer...       UNK          2  
17423  Covid Pfizer Vaccine was stored in the freezer...       UNK          2  
17424  Covid Pfizer Vaccine was stored in the freezer...       UNK          2  

[17425 rows x 6 columns]

In [ ]:
df_symptoms_covid.columns = df_symptoms_covid.columns.str.strip()


Exploring tokenization with Ollama (a benchmark for all LLM models henceforth)

In [23]:
import ollama
response = ollama.chat(model='llama3.1', messages=[
  {
    'role': 'user',
    'content': 'Hey how are you?',
  },
])
print(response['message']['content'])



I'm just a computer program, so I don't have feelings or emotions like humans do. But thank you for asking! How can I help you today?


In [73]:
df_symptoms_covid['SYMPTOM_LIST'] = ''

In [76]:
import ollama
for i in range(len(df_symptoms_covid)):
  text = df_symptoms_covid['SYMPTOM_TEXT'][i]
  response = ollama.chat(model='llama3.1', messages=[
    {
      'role': 'system',
      'content': 'You are a helpful ai bot in the field of bio research and you are working on a vaccine symptoms dataset. You will help out enlisting symptoms in the order of their occurence in the patient from the given symptom freetext. Please make sure your response doesnt include anything else other than the list of symptoms. It should be one or two words persymptom, in the order of their occurence. For example : fever, cough, arthritis, pain in the lower back, hospitalization so your text should look like <symptom1> , <sympotom2>, <symptom3> and so on. You cannot return any response other than symptom mentioned the freetext. if you dont find a symptom, return NA',
      'role':'user',
      'content':f'heres one of the free text entries from the dataset, I only need the list of symptoms from this data, please return a comma separated list. Dont return any text before or after the list other than the tokens in the list. {text}',
    },
  ])
  # data['response'] = response['message']['content']
  df_symptoms_covid['SYMPTOM_LIST'] = response['message']['content']
  print(response['message']['content'])

muscle at the injection site is sore, He cannot lift anything more than 5 pounds., Arm soreness
arrest in speech, eye rolling, arm stiffness, seizures
fever, chills, unknown spot on lung
fever, chills, spot on lung
fever, chills, endocarditis, lung spot
fever, aches and pains, fatigue, chills, night sweats, diarrhea, loss of appetite, fever, fatigue, diarrhea, loss of appetite
shoulder pain, prolonged pain, no resolution
hives, itching, rash
lumps, thighs, wrist, arm
brain was in a fog, thinking was slowed, flu symptoms (for 24hrs), took more effort than usual
Here is the list of symptoms in a comma-separated format:

shortness of breath, fevers, respiratory distress, tachycardia, hypotension, mild fever, anxiety, urinary incontinence, dysphagia, left shoulder pain, sore throat (implied by tracheostomy), fatigue (implied by chronic respiratory failure)
floaters, impaired vision, retinal tear, detached retina
Here is the list of symptoms as a comma-separated string:

chest pain, epigast

KeyboardInterrupt: 

In [ ]:
data #the responses were not consistent and the model failed to understand the mechanism of the task at hand

{'text': 'Migraine, nausea, tachycardia, L leg pain and pulling (front of thigh, back of calf), heaviness of heart, SOB, irritability, fatigue,',
 'response': 'Here is the list of symptoms as a comma-separated list:\n\nMigraine, nausea, tachycardia, L leg pain, pulling (front of thigh, back of calf), heaviness of heart, SOB, irritability, fatigue'}

In [50]:
df_symptoms_covid['SYMPTOM_LIST'] = ''

Exploring NER Models, en_ner_bc5cdr without replacing medical abbreviations


In [69]:
import spacy
import scispacy

# Load ScispaCy model
nlp = spacy.load("en_ner_bc5cdr_md")  # Use a medical-specific model

# Example VAERS text data
# text = "Patient experienced headache, nausea, and muscle pain following vaccination."
for i in range(1020, len(df_symptoms_covid)):
    text = df_symptoms_covid['SYMPTOM_TEXT'][i]
    # Process the text
    doc = nlp(text)

    # Extract entities labeled as symptoms
    symptoms = [ent.text for ent in doc.ents if ent.label_ == "DISEASE"]
    print("Extracted Symptoms:", symptoms)
    df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms


/Users/snehadharne/anaconda3/lib/python3.11/site-packages/spacy/util.py:910: UserWarning: [W095] Model 'en_ner_bc5cdr_md' (0.4.0) was trained with spaCy v3.0.1 and may not be 100% compatible with the current version (3.7.2). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


Extracted Symptoms: []
Extracted Symptoms: []
Extracted Symptoms: ['breast cancer', 'breast cancer']
Extracted Symptoms: []


/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/ind

Extracted Symptoms: ['depression']
Extracted Symptoms: ['allergies']
Extracted Symptoms: ['allergies']
Extracted Symptoms: ['aches', 'fever', 'fever']


/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/ind

...

/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/ind

Extracted Symptoms: ['vitiligo', 'vitiligo']
Extracted Symptoms: ['tinnitus', 'tinnitus', 'tinnitus', 'tinnitus', 'Tinnitus', 'tinnitus', 'tinnitus', 'tinnitus', 'tinnitus', 'small vessel disease', 'tinnitus', 'symptoms/events']
Extracted Symptoms: []
Extracted Symptoms: []
Extracted Symptoms: []
Extracted Symptoms: []


/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/ind

Extracted Symptoms: []
Extracted Symptoms: []


/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms
/var/folders/ck/hmsclsfj6y1d_pbb28pqpv_h0000gn/T/ipykernel_39017/2132984947.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_symptoms_covid['SYMPTOM_LIST'][i] = symptoms


In [68]:
df_symptoms_covid['SYMPTOM_LIST'][1030]

["Crohn's disease",
 'allergy',
 'panuveitis',
 'allergy',
 'allergy',
 'allergy',
 'allergy']

In [70]:
df_symptoms_covid

Unnamed: 0  VAERS_ID VAX_TYPE   
0               0   2728994  COVID19  \
1               1   2729004  COVID19   
2               2   2729006  COVID19   
3               3   2729006  COVID19   
4               4   2729006  COVID19   
...           ...       ...      ...   
17420       17551   2802236  COVID19   
17421       17552   2802237  COVID19   
17422       17553   2802238  COVID19   
17423       17554   2802239  COVID19   
17424       17555   2802240  COVID19   

                                            SYMPTOM_TEXT V_ADMINBY  FORM_VERS   
0      muscle at the injection site is sore; He canno...       PHM          2  \
1      Micro-seizures starting approximately 2 weeks ...       OTH          2   
2      On September 14, 2023, I was admitted to Hospi...       PHM          2   
3      On September 14, 2023, I was admitted to Hospi...       PHM          2   
4      On September 14, 2023, I was admitted to Hospi...       PHM          2   
...                                                  ...       ...        ...   
17420  Covid Pfizer Vaccine was stored in the freezer...       UNK          2   
17421  Covid Pfizer Vaccine was stored in the freezer...       UNK          2   
17422  Covid Pfizer Vaccine was stored in the freezer...       UNK          2   
17423  Covid Pfizer Vaccine was stored in the freezer...       UNK          2   
17424  Covid Pfizer Vaccine was stored in the freezer...       UNK          2   

                                            SYMPTOM_LIST  
0      [sore, muscle pain, muscle pain, sore, pain, m...  
1      [Seizures, seizure, auto-immune disease, Encep...  
2             [Endocarditis, strep mitis, fever, chills]  
3             [Endocarditis, strep mitis, fever, chills]  
4             [Endocarditis, strep mitis, fever, chills]  
...                                                  ...  
17420                                                 []  
17421                                                 []  
17422                                                 []  
17423                                                 []  
17424                                                 []  

[17425 rows x 7 columns]

In [71]:
df_symptoms_covid.to_csv('symptoms_covid_list.csv')

In [ ]:
#saved the tokenized data for EDA